## Objective

The aim of this notebook is generate the P-Space graph from the cleaned L-Space graph

### Pre-requisites

In [12]:
import os
import sys

sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '../../')))

from utils.imports import *

### Load L-Space Graph

In [13]:
attributes = load_gtfs(str(BASE_DIR / "sqlite/NL.sqlite"))

In [14]:
L_graph=load_graph(DATA_DIR / "pkl/nl_merged.pkl")
plot_graph(L_graph, back_map="OSM")

## Create P-Space Graph

In [4]:
P_graph=P_space_v4(attributes,
          L_graph,
          start_hour=5, # Same as when building L-space
          end_hour=24, # Same as when building L-space
          mode="Rail") # Same as when building L-space

plot_graph(P_graph,"P")

In [5]:
# save_graph(P_graph,DATA_DIR / "pkl/nl_P.pkl") # Saving the P-Graph

## Load P-Space Graph

In [6]:
P_graph=load_graph(DATA_DIR / "pkl/nl_P.pkl")
# plot_graph(P_graph,"P")

### Compute shortests paths between all pairs of nodes.
#### Note: this may take several minutes (depending on the size of the graph)
For a given pair of nodes $i$ and $j$, This function computes $sp_1,\ldots, sp_m$, the $m$ shortest paths in $\mathbf{L}$-space, i.e., the shortest in terms of in-vehicle travel time, for each pair of nodes $i$ and $j$

The GTC between pairs of stops accounts for initial and transfer waiting times, in-vehicle travel times, and a time-equivalent penalty cost for transfers.

For each path in L-space, we compute the sum of the waiting times for each leg in the path and the number of transfers, according to the labels and number of hops of the corresponding paths in $\mathbf{P}$-space. 
The GTC is determined by the following weighted sum:

$  \text{GTC}(sp_i)= {\text{in_vehicle_time}(sp_i) + \mathbf{\alpha} \times \text{waiting_time}(sp_i) + \sum_{j=1}^{{\text{n_transfers}}(sp_i)}{\beta_J}}$

In [7]:
import time

# Start timing
start_time = time.time()

# Waiting penalty (multiplier)
alpha = 2  # Waiting time is multiplied by 2

# Transfer penalties in minutes. Arbitrary size of at least one element, with the minutes to add
# for the first, second, third... transfers. 
betas = [5]  # 5 minutes for the first transfer
# betas = [5,15]  # 5 minutes for the first transfer, 15 minutes for any transfer after that.

# Number of shortest paths to retrieve
m = 3

gtc = get_all_GTC_v4(L_graph, P_graph, m, alpha, betas)

# End timing
end_time = time.time()

print(f"Execution time: {end_time - start_time:.4f} seconds")

Execution time: 9.3435 seconds


In [9]:
save_gtc_to_pkl(gtc, DATA_DIR / "pkl/gtc_data_netherlands.pkl")

GTC data saved to C:\Users\KIIT\Documents\UAntwerp\railways_resilience\data\pkl\gtc_data_netherlands.pkl


In [10]:
gtc_loaded = load_gtc_from_pkl(DATA_DIR / "pkl/gtc_data_netherlands.pkl")

GTC data loaded from C:\Users\KIIT\Documents\UAntwerp\railways_resilience\data\pkl\gtc_data_netherlands.pkl


#### Understanding the results

For each pair of nodes we get as many paths as requested (or as many as available if there are fewer alternative paths).

The results is a dictionary, indexed by the nodes of origin (first index) and the nodes of destination (second index). For each pair of nodes we get a list, with the alternative paths ordered by GTC.

Each path is again modeled as a dictionary, including the following attributes:
- path: the sequence of nodes in the path computed in the L-space graph
- GTC: the GTC corresponding to that path
- in_vehicle: the in-vehicle travel time in minutes of that path
- waiting_time: the waiting-time in minutes of that path (from P-space)
- n_transfers: the number of transfers of that path (hops in P-space)

In [11]:
#Example: check the GTC between nodes 51 and 37
gtc_loaded[50][37]

{'path': [50,
  51,
  52,
  53,
  54,
  55,
  203,
  204,
  205,
  56,
  206,
  207,
  96,
  97,
  98,
  22,
  21,
  40,
  39,
  38,
  37],
 'GTC': 221,
 'in_vehicle': 111,
 'waiting_time': 50,
 'n_transfers': 2,
 'traveled_distance': 146550}